In [105]:
import pandas as pd
pd.options.mode.chained_assignment = None
import numpy as np
import sqlite3
import csv
!pip install plotly
import plotly
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots
import datetime as dt

In [106]:
print('Содержание.\n\
1. Подключение и краткое описание Dataframe Google Play Store Apps.\n\
2. Подготовка и оптимизациядля для дальнейшего анализа.\n\
3. Список самых популярных приложений по категориям.\n\
4. Самые дорогие приложения и категории.\n\
5. Категории, содержащие самое большое количество приложений без отзывов.\n\
6. Доля платных приложений в Google Play. Store\n\
7. Самые популярные категории приложений в Google Play Store. \n\
8. Динамика увеличения колиства приложений по категориям за последние 8 лет.\n\
9. Инвестиционная привлекательность. \n\
10. Кореляция рейтинга приложений по категориям в Google Play Store. \n\
')

Содержание.
1. Подключение и краткое описание Dataframe Google Play Store Apps.
2. Подготовка и оптимизациядля для дальнейшего анализа.
3. Список самых популярных приложений по категориям.
4. Самые дорогие приложения и категории.
5. Категории, содержащие самое большое количество приложений без отзывов.
6. Доля платных приложений в Google Play. Store
7. Самые популярные категории приложений в Google Play Store. 
8. Динамика увеличения колиства приложений по категориям за последние 8 лет.
9. Инвестиционная привлекательность. 
10. Кореляция рейтинга приложений по категориям в Google Play Store. 



In [107]:
#1. Подключение и краткое описание Dataframe Google Play Store Apps.
df0 = pd.read_csv("C://Google-Playstore.csv")
str = df0.shape[0]
col = df0.shape[1]
qnt_categ  = len(df0['Category'].unique())
print(f'Представляю вниманию базу данных с приложениями из Google Play Store. \
База представляет собой список из {str} приложений и {col - 1} параметров данных приложений.\
Все приложения разделены на {qnt_categ} категорий.\
Ниже представлена часть указанного дата сэта для визуального ознакомления:\
')
df0.head(5)

Представляю вниманию базу данных с приложениями из Google Play Store. База представляет собой список из 2312944 приложений и 23 параметров данных приложений.Все приложения разделены на 48 категорий.Ниже представлена часть указанного дата сэта для визуального ознакомления:


App_Name  \
0                                            Gakondo   
1                                Ampere Battery Info   
2                                             Vibook   
3  Smart City Trichy Public Service Vehicles 17UC...   
4                                            GROW.me   

                       App_Id       Category  Rating  Rating_Count Installs  \
0         com.ishakwe.gakondo      Adventure     0.0           0.0      10+   
1  com.webserveis.batteryinfo          Tools     4.4          64.0   5,000+   
2        com.doantiepvien.crm   Productivity     0.0           0.0      50+   
3     cst.stJoseph.ug17ucs548  Communication     5.0           5.0      10+   
4        com.horodyski.grower          Tools     0.0           0.0     100+   

   Minimum_Installs  Maximum_Installs  Free  Price  ...  \
0              10.0                15  True    0.0  ...   
1            5000.0              7662  True    0.0  ...   
2              50.0                58  True    0.0  ...   
3              10.0                19  True    0.0  ...   
4             100.0               478  True    0.0  ...   

                  Developer_Website              Developer_Email  \
0       https://beniyizibyose.tk/#/       jean21101999@gmail.com   
1   https://webserveis.netlify.app/         webserveis@gmail.com   
2                               NaN          vnacrewit@gmail.com   
3  http://www.climatesmarttech.com/  climatesmarttech2@gmail.com   
4       http://www.horodyski.com.pl    rmilekhorodyski@gmail.com   

       Released  Last_Updated Content_Rating  \
0  Feb 26, 2020  Feb 26, 2020       Everyone   
1  May 21, 2020  May 06, 2021       Everyone   
2   Aug 9, 2019  Aug 19, 2019       Everyone   
3  Sep 10, 2018  Oct 13, 2018       Everyone   
4  Feb 21, 2020  Nov 12, 2018       Everyone   

                                      Privacy_Policy Ad_Supported  \
0                 https://beniyizibyose.tk/projects/        False   
1  https://dev4phones.wordpress.com/licencia-de-uso/         True   
2  https://www.vietnamairlines.com/vn/en/terms-an...        False   
3                                                NaN         True   
4                        http://www.horodyski.com.pl        False   

  In_App_Purchases Editors_Choice         Scraped_Time  
0            False          False  2021-06-15 20:19:35  
1            False          False  2021-06-15 20:19:35  
2            False          False  2021-06-15 20:19:35  
3            False          False  2021-06-15 20:19:35  
4            False          False  2021-06-15 20:19:35  

[5 rows x 24 columns]

In [108]:
#2. Подготовка и оптимизациядля для дальнейшего анализа.
print('Для оптимизации работы с нашим дата сэтом выполним несколько шагов:\n\
1. Проверим наличие NaN в столбцах, которые будут использованы для последующих вычислений.\n\
   Удалим строки содержащие NaN \n\
2. Удалим столбцы, которые нам не потребуются для анализа:\n\
    App_Id, Installs, Minimum_Installs, Developer_Website, Developer_Email, Last_Updated,\n\
    Content_Rating, Privacy_Policy, Ad_Supported, In_App_Purchases, Scraped_Time, Size,\n\
3. Добавим столбцы, которые далее потребуются для анализа и постоения графиков.\n\
   Значения будут вычислены на основе имеющихся данных: \n\
    Released_Year - год релиза приложения \n\
    Lifetime - "возраст" приложения в месяцах \n\
    revenue_per_month - объем выручки, которое приносит приложение, \n\
      без учета встроенных покупок \n\
    Avr_installs_per_month - среднее количество установок приложения в месяц \n\
    Price_USD - цена приложения сконвертированная в USD\n\
\n\
Столбцы содержащие NaN:\
')

print(df0.isna().sum())
df0 = df0.dropna(axis='index', how='any', subset=['Released', 'Rating', 'Rating_Count', 'Currency'])
df0['Released_Year'] = pd.Series(df0['Released'].str[7:].tolist()).values
df0['Released_Year'] = df0['Released_Year'].str.replace(' ', '')
df0['Released'] = pd.to_datetime(df0['Released'], dayfirst=True)
d = pd.to_datetime('2021-07-16')
df0['Lifetime'] = 12 * (d.year - df0['Released'].dt.year) + d.month - df0['Released'].dt.month      
df0['Avr_installs_per_month'] = df0['Maximum_Installs']/df0['Lifetime']
df0['Currency'].unique()
df0.loc[df0['Currency'] == 'USD', 'Currency'] = 1
df0.loc[df0['Currency'] == 'XXX', 'Currency'] = 1
df0.loc[df0['Currency'] == 'CAD', 'Currency'] = 0.8
df0.loc[df0['Currency'] == 'EUR', 'Currency'] = 1.19
df0.loc[df0['Currency'] == 'INR', 'Currency'] = 0.013
df0.loc[df0['Currency'] == 'nan', 'Currency'] = 1
df0.loc[df0['Currency'] == 'VND', 'Currency'] = 0.000043
df0.loc[df0['Currency'] == 'GBP', 'Currency'] = 1.29
df0.loc[df0['Currency'] == 'BRL', 'Currency'] = 0.19
df0.loc[df0['Currency'] == 'KRW', 'Currency'] = 0.00087
df0.loc[df0['Currency'] == 'TRY', 'Currency'] = 0.12
df0.loc[df0['Currency'] == 'RUB', 'Currency'] = 0.13
df0.loc[df0['Currency'] == 'SGD', 'Currency'] = 0.74
df0.loc[df0['Currency'] == 'AUD', 'Currency'] = 0.75
df0.loc[df0['Currency'] == 'PKR', 'Currency'] = 0.0063
df0.loc[df0['Currency'] == 'ZAR', 'Currency'] = 0.069
df0['Price_USD'] = df0['Price']*df0['Currency'] 
df0['revenue_per_month'] = (df0['Maximum_Installs']/df0['Lifetime']*df0['Price_USD'])/1000000 
df0.drop(['App_Id', 'Privacy_Policy', 'Installs', 'Minimum_Installs', 'Developer_Website',
'Developer_Email', 'Last_Updated', 'Content_Rating', 'Privacy_Policy', 'Ad_Supported',
'In_App_Purchases', 'Scraped_Time', 'Size', 'Minimum_Android','Developer_Id'], axis=1, inplace=True)
print(df0.isna().sum())

Для оптимизации работы с нашим дата сэтом выполним несколько шагов:
1. Проверим наличие NaN в столбцах, которые будут использованы для последующих вычислений.
   Удалим строки содержащие NaN 
2. Удалим столбцы, которые нам не потребуются для анализа:
    App_Id, Installs, Minimum_Installs, Developer_Website, Developer_Email, Last_Updated,
    Content_Rating, Privacy_Policy, Ad_Supported, In_App_Purchases, Scraped_Time, Size,
3. Добавим столбцы, которые далее потребуются для анализа и постоения графиков.
   Значения будут вычислены на основе имеющихся данных: 
    Released_Year - год релиза приложения 
    Lifetime - "возраст" приложения в месяцах 
    revenue_per_month - объем выручки, которое приносит приложение, 
      без учета встроенных покупок 
    Avr_installs_per_month - среднее количество установок приложения в месяц 
    Price_USD - цена приложения сконвертированная в USD

Столбцы содержащие NaN:
App_Name                  2
App_Id                    0
Category                

In [96]:
#3. Список самых популярных приложений по категориям.
conn = sqlite3.connect('C://GPStore.sqlite')
c = conn.cursor()
request = "CREATE TABLE GPS2('App_Name','Category','Rating','Rating_Count','Maximum_Installs',\
'Free','Price','Currency','Released','Editors_Choice','Released_Year','Lifetime',\
'revenue_per_month','Avr_installs_per_month','Price_USD')"
c.execute(request)
conn.commit()
df0.to_sql('GPS2', conn, if_exists='append', index=False)

App_Name   Category
0                           Garena Free Fire - Rampage     Action
1                                         Temple Run 2     Action
2         Sniper 3D: Fun Free Online FPS Shooting Game     Action
3                               PUBG MOBILE - Traverse     Action
4                                               Roblox  Adventure
..                                                 ...        ...
187   AccuWeather: Weather alerts & live forecast info    Weather
188  Words of Wonders: Crossword to Connect Vocabulary       Word
189                       CodyCross: Crossword Puzzles       Word
190                  Words Story - Addictive Word Game       Word
191                                        Word search       Word

[192 rows x 2 columns]

In [97]:
pd.read_sql("""
select App_Name, Category from (
select *, row_number() over (partition by Category order by Maximum_Installs desc) as rn
from GPS2)
where rn < 5
""", conn).head(20)

App_Name   Category
0                    Garena Free Fire - Rampage     Action
1                                  Temple Run 2     Action
2  Sniper 3D: Fun Free Online FPS Shooting Game     Action
3                        PUBG MOBILE - Traverse     Action
4                                        Roblox  Adventure
5                                    Pokémon GO  Adventure
6                                 Criminal Case  Adventure
7                               Kiloblocks Lite  Adventure
8                                Subway Surfers     Arcade
9                                    Temple Run     Arcade

In [98]:
#4. Какие приложения самые дорогие (и категории)
pd.read_sql("""select App_Name, Category, max(price_USD) Price
from (select * from gps2)
group by Category""", conn)

App_Name  \
0                          INFESTED OLD - Horror Game   
1                                               英雄出征2   
2                   Challenge Impossible Ball for you   
3           10.000 Moving Cities – Same but Different   
4                                 REPUVE y mas... PRO   
5   Golden Ratio Face - Beauty Analysis & Beauty Tips   
6                            Most expensive word game   
7                                      secret of life   
8                                               Taxes   
9                               The Preflop Advantage   
10                             Blackjack Verite Games   
11                             Most Expensive Clicker   
12                          Perfect Viewer Donation 3   
13                                           Autocopy   
14                                   Nu Media TV Live   
15                                          PSC Login   
16                                       Math vs Bath   
17                                            Luxsure   
18                                                Awe   
19            VahiKhatu - Track Borrowed / Lent Money   
20          how to dressed up Low carb Vietnamese pho   
21                              Acid Reflux Treatment   
22     Cannabis Grow App Garden Plants Guide Tool Pro   
23                           Hide Something - License   
24                                            Why Not   
25                                     Точки интереса   
26      Autism & Pervasive Developmental Disorders 4e   
27                                      Café Twilight   
28                                               AudD   
29                                           Hn3 news   
30        Bit Guardian Parental Control - For Parents   
31                                    INFINITY STONES   
32  LockMyPix Photo Vault PRO: Hide Photos and Videos   
33                                       MESH Connect   
34                         Plasma duct - Premium Game   
35                     Virtual Race Car Engineer 2018   
36                              MR Beast ( Fan Game )   
37     Premium Luxury Watches - Luxury Watches Brands   
38                     Presidential Election Campaign   
39                                           RichWall   
40                   Mega Tips Bet Premium (LifeTime)   
41                                  WARSURGE LIFETIME   
42                                           TEST EGY   
43                     PathAway PRO Outdoor Navigator   
44                           The Jackbox Party Pack 5   
45                     Training Avid Media Composer 7   
46                     Weather - Routing - Navigation   
47                          Most Expensive Wordsearch   

                   Category   Price  
0                    Action   59.99  
1                 Adventure   29.99  
2                    Arcade  399.99  
3              Art & Design  354.99  
4           Auto & Vehicles  294.99  
5                    Beauty   14.99  
6                     Board  399.99  
7         Books & Reference  399.99  
8                  Business  399.99  
9                      Card   74.99  
10                   Casino   34.99  
11                   Casual  399.99  
12                   Comics    9.99  
13            Communication   99.99  
14                   Dating  399.99  
15                Education  364.99  
16              Educational  294.99  
17            Entertainment  399.99  
18                   Events   11.99  
19                  Finance  199.99  
20             Food & Drink  249.99  
21         Health & Fitness  399.99  
22             House & Home   17.99  
23         Libraries & Demo   19.99  
24                Lifestyle  399.99  
25        Maps & Navigation  399.99  
26                  Medical  365.99  
27                    Music    9.49  
28            Music & Audio  399.99  
29         News & Magazines    9.99  
30                Parenting   10.99  
31          Personalization  279.99

In [99]:
#5. Какие категории содержат самое большое количество приложений без отзывов
pd.read_sql("""select App_Name, Category, count(Editors_Choice) Without_Editors_Choice
from GPS2
where Editors_Choice = 0
group by Category
order by Without_Editors_Choice desc
""", conn)

App_Name  \
0                   Calculus Tutorial 1: Introduction   
1                                        Radio Louvor   
2                                 Ampere Battery Info   
3                                      Kamesh Welding   
4                               Coloring Book Barbaie   
5                               The Everyday Calendar   
6                      Contemporary Love Wallpaper HD   
7                    Neon 3d Iron Tech Keyboard Theme   
8                                     Head Lice guide   
9                                              Vibook   
10                                          BuradaOto   
11                              Readymade Grocery App   
12                     桃園機場捷運時刻表 - 捷運轉乘路線快速查詢(支援台北捷運)   
13                                               VİOP   
14                                        Sticky Ball   
15                            Block Fill: Puzzle Game   
16                                        Coffin Move   
17  Smart City Trichy Public Service Vehicles 17UC...   
18                          Bowling Paradise Pro FREE   
19                                             IMOCCI   
20                                              op.se   
21       Photo Brightness Editor - Image Brighten App   
22                                  Bhavan's BHEL VIM   
23                                               忍者道場   
24                                            Parents   
25                                 Extreme Flight Sim   
26                                            Gakondo   
27                                  Chemistry Mission   
28    Flyers, Posters, Banner, Graphic Maker, Designs   
29                                  Cambodian.Express   
30                                         عون | Awon   
31        HD Video Player (IPTV) Mp4 Max - All Format   
32                                             ignite   
33                              Let's Fact? Let's Go!   
34                        Camelia Estetica & Solarium   
35                                    Bounce & Bubble   
36                                    Dodge The Cars!   
37                                       Duo+ Hangout   
38                                  Bible Word Search   
39                             The Brownie Strategist   
40                                               Trix   
41    Mega Ramps Car Stunts: Ultimate Races Car Games   
42                                 Infinity Loves ATL   
43                   unlimited 4G data prank free app   
44                                    Casino High Low   
45        Marshmello Alone Launchpad Mashup Music Mix   
46                                        ParentingNI   
47   Freedom Army Zombie Shooter 2: Free FPS Shooting   

                   Category  Without_Editors_Choice  
0                 Education                  241050  
1             Music & Audio                  154894  
2                     Tools                  143987  
3                  Business                  143761  
4             Entertainment                  138259  
5                 Lifestyle                  118316  
6         Books & Reference                  116720  
7           Personalization                   89210  
8          Health & Fitness                   83469  
9              Productivity                   79683  
10                 Shopping                   75229  
11             Food & Drink                   73903  
12           Travel & Local                   67265  
13                  Finance                   65449  
14                   Arcade                   53774  
15                   Puzzle                   51102  
16                   Casual                   50769  
17            Communication                   48160  
18                   Sports                   47450  
19                   Social                   44724  
20         News & Magazines                   42790  
21              Photography                   35543  
22       

In [86]:
#Переменные для постоения дальнейших графиков
qnt_paid_apps = len(df0[df0['Free'] == 0])
qnt_free_apps = len(df0[df0['Free'] == 1])
free_counts = df0['Free'].value_counts()
most_installs_cat = df0.groupby(['Category'])['Maximum_Installs'].sum().sort_values(ascending=False)
gr_qnt_paid_apps = df0.loc[df0['Free'] == 0].groupby(["Category"])['Free'].size().reset_index()
gr_qnt_apps = df0.groupby(["Category"])['Free'].size().reset_index()
perc_of_paid = (gr_qnt_paid_apps['Free']/gr_qnt_apps['Free'])*100
revenue_per_month_cat = df0.groupby(['Category'])['revenue_per_month'].sum().sort_values(ascending=False)

In [87]:
#6. Доля платных приложений в Google Play. Store
print('Нижеследующая диаграмма показывает, что доля платных приложений составляет всего лишь 1.95%')

Нижеследующая диаграмма показывает, что доля платных приложений составляет всего лишь 1.95%


In [88]:
fig = go.Figure()
fig.add_trace(go.Pie(values=free_counts, labels=['бесплатные', 'платные']))
fig.update_layout(
    title="Доля платных приложений",
    title_x = 0.5,
    margin=dict(l=0, r=0, t=30, b=0),
    legend_orientation="h")
fig.show()

In [89]:
print('В разрезе категорий видим, что наиболее высокая доля платных приложений\
в категориях:\n\
Role playing - 6.9% \n\
Strategy - 6.7% \n\
Personalization - 6.4% \n\
')
data = [go.Bar(
   x = gr_qnt_paid_apps['Category'].tolist(),
   y = perc_of_paid.tolist()
)]
fig = go.Figure(data=data)
fig.update_layout(
    title="Доля платных платных приложений по категориям",
    title_x = 0.5,
    margin=dict(l=0, r=0, t=30, b=0),
    legend_orientation="h")
fig.show()

В разрезе категорий видим, что наиболее высокая доля платных приложенийв категориях:
Role playing - 6.9% 
Strategy - 6.7% 
Personalization - 6.4% 



In [90]:
#7. Самые популярные категории приложений в Google Play Store. 
print('График ниже показывает, что чаще всего скачивают приложения в категориях:\n\
Tools - 119B \n\
Communication - 72B \n\
Productivity - 45B \n\
')
data = [go.Bar(
   x = most_installs_cat.index.tolist(),
   y = most_installs_cat.tolist()
)]
fig = go.Figure(data=data)
fig.update_layout(
    title="Самые скачиваемые категории",
    title_x = 0.5,
    margin=dict(l=0, r=0, t=30, b=0),
    legend_orientation="h")
fig.show()

График ниже показывает, что чаще всего скачивают приложения в категориях:
Tools - 119B 
Communication - 72B 
Productivity - 45B 



In [91]:
#8. Динамика увеличения колиства приложений по категориям за последние 8 лет.
print('График ниже показывает, что за последние 8 лет категории Education лидирует\
по количеству релизов новых приложений. Категории Tools и Book&Reference \n\
за последние 8 лет сместилась на 5е и 6е места соответственно.\n\
Тенденция к увеличению релизов наблюдается у категорий Music и Busines \n\
В 2020 году они поднялись на 2е и 3е место соответственно\
')
num_steps = 8
trace_list = [go.Bar(visible=True,
   x = df0.loc[df0['Released_Year'] == '2013'].groupby(["Category"])['Free'].size().reset_index().sort_values(by='Free', ascending=False).head(10)['Category'].tolist(),
   y = df0.loc[df0['Released_Year'] == '2013'].groupby(["Category"])['Free'].size().reset_index().sort_values(by='Free', ascending=False).head(10)['Free'].tolist())]
for i in range(2013, 2020):
    trace_list.append(go.Bar(visible=False,
   x = df0.loc[df0['Released_Year'] == (f'{i}')].groupby(["Category"])['Free'].size().reset_index().sort_values(by='Free', ascending=False).head(10)['Category'].tolist(),
   y = df0.loc[df0['Released_Year'] == (f'{i}')].groupby(["Category"])['Free'].size().reset_index().sort_values(by='Free', ascending=False).head(10)['Free'].tolist()))
fig = go.Figure(data=trace_list)
steps = []
for i in range(num_steps):
    # Hide all traces
    year = dict(
        method = 'restyle',  
        args = ['visible', [False] * len(fig.data)],
    )
    # Enable trace we want to see
    year['args'][1][i] = True
    
    # Add step to step list
    steps.append(year)

sliders = [dict(
    steps = steps,
)]

fig.layout.sliders = sliders

fig.show()

График ниже показывает, что за последние 8 лет категории Education лидируетпо количеству релизов новых приложений. Категории Tools и Book&Reference 
за последние 8 лет сместилась на 5е и 6е места соответственно.
Тенденция к увеличению релизов наблюдается у категорий Music и Busines 
В 2020 году они поднялись на 2е и 3е место соответственно


In [92]:
#9. Инвестиционная привлекательность.
print('График ниже показывает, что игровые категории приносят наибольшую выручку разработчикам, около 20 млн.долл.в месяц \n\
2е место занимает категория Tools - 2.5 млн.долл.в месяц \n\
3е место делят с примерно одинаковым объемом выручки категории Education и Music - 1.6 млн.долл. в месяц \n\
')
data = [go.Bar(
   x = revenue_per_month_cat.index.tolist(),
   y = revenue_per_month_cat.tolist()
)]
fig = go.Figure(data=data)
fig.update_layout(
    title="Самые доходные  категории",
    title_x = 0.5,
    margin=dict(l=0, r=0, t=30, b=0),
    legend_orientation="h")
fig.show()

График ниже показывает, что игровые категории приносят наибольшую выручку разработчикам, около 20 млн.долл.в месяц 
2е место занимает категория Tools - 2.5 млн.долл.в месяц 
3е место делят с примерно одинаковым объемом выручки категории Education и Music - 1.6 млн.долл. в месяц 



In [ ]:
#10. Кореляция рейтинга приложений по категориям в Google Play Store. 
# при загрузке графика выходит ошибка памяти, хотя вроде ноут норм по производительности, 
#но почему-то при построении съедается оперативка 16ГБ
#ниже код, который хотелось бы как-то запустить


px.scatter(df0, x="Lifetime", y="Rating_Count", animation_frame="Rating",
           size="Avr_installs_per_month", hover_name="Category",
           log_x=True, size_max=150, range_x=[1,145], range_y=[0,4200000])

In [109]:
#10. Кореляция рейтинга приложений по категориям в Google Play Store. (*только по платным приложениям)
#аналогичный тип графика запускается, если брать меньший df, содержащий только платные приложения
df1 = df0.loc[df0['Free'] == 0]
px.scatter(df1, x="Lifetime", y="Rating_Count", animation_frame="Rating",
           size="Avr_installs_per_month", hover_name="Category",
           log_x=True, size_max=150, range_x=[1,145], range_y=[0,4200000])